In [3]:
import numpy as np
import argparse
import pandas as pd
import glob
import datetime
import matplotlib.pyplot as plt
import act
import os
import sys
sys.path.append('../')
from tempfile import TemporaryDirectory
import altair as alt

In [6]:
USERNAME = os.getenv("ARM_USERNAME")
TOKEN = os.getenv("ARM_TOKEN")
SAIL_DATA_STREAM = 'gucdlprofwind4newsM1.c1'
DATA_STREAM_FILEEXT = '.nc'
startdate = "2022-01-01"
enddate = "2022-12-31"
output_dir = os.path.join("/data2/elilouis/sublimationofsnow/", SAIL_DATA_STREAM)

In [7]:
act.discovery.download_data(USERNAME, TOKEN, SAIL_DATA_STREAM, startdate, enddate, output=output_dir)

[DOWNLOADING] gucdlprofwind4newsM1.c1.20221125.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20221126.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20221127.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20221128.000039.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20221129.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20221130.000039.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20221201.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220101.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220102.000041.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220103.000041.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220104.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220105.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220106.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220107.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220108.000040.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220109.000041.nc
[DOWNLOADING] gucdlprofwind4newsM1.c1.20220111.000040.nc
[DOWNLOADING] gucdlprofwind4new

['/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221125.000040.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221126.000040.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221127.000040.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221128.000039.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221129.000040.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221130.000039.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20221201.000040.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20220101.000040.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM1.c1/gucdlprofwind4newsM1.c1.20220102.000041.nc',
 '/data2/elilouis/sublimationofsnow/gucdlprofwind4newsM

In [12]:
dl_prof_files = glob.glob(os.path.join(output_dir,'*'+DATA_STREAM_FILEEXT))
print(len(dl_prof_files))

364


In [13]:
dl_prof = act.io.armfiles.read_netcdf(dl_prof_files)

In [16]:
src_prof = dl_prof.to_dataframe().query('bound==0')
src_prof = src_prof.reset_index().set_index('time').tz_localize("UTC").tz_convert("US/Mountain").tz_localize(None)

src_prof = src_prof.reset_index()[['time', 'height','wind_speed', 'wind_speed_error',
       'wind_direction', 'wind_direction_error', ]]

In [48]:
df_200 = src_prof.query("height < 200").groupby("time").median().resample("60Min").median().reset_index()
df_600 = src_prof.query("height < 600").groupby("time").median().resample("60Min").median().reset_index()

In [49]:
df_200 = df_200[df_200['time'].dt.year==2022]
df_600 = df_600[df_600['time'].dt.year==2022]

In [50]:
df_200

time      height  wind_speed  wind_speed_error  \
7    2022-01-01 00:00:00  140.953899    3.008595          0.225998   
8    2022-01-01 01:00:00  140.953899    3.649757          0.210511   
9    2022-01-01 02:00:00  140.953899    3.750187          0.140389   
10   2022-01-01 03:00:00  140.953899    1.579083          0.173534   
11   2022-01-01 04:00:00  140.953899    5.573896          0.289197   
...                  ...         ...         ...               ...   
8731 2022-12-30 12:00:00  140.953899    2.490951          0.527506   
8732 2022-12-30 13:00:00  140.953899    2.182926          0.506093   
8733 2022-12-30 14:00:00  140.953899    1.392240          0.199241   
8734 2022-12-30 15:00:00  140.953899    1.681792          0.382257   
8735 2022-12-30 16:00:00  140.953899    1.817812          0.341196   

      wind_direction  wind_direction_error  
7         336.383057              3.947169  
8         339.671387              2.694670  
9         346.618530              2.448627  
10        316.503174              6.898115  
11        343.441528              3.501023  
...              ...                   ...  
8731      268.977692             13.156557  
8732      164.864899             15.233782  
8733      121.611008              9.792706  
8734      285.261658             16.919088  
8735      168.267731             12.131224  

[8729 rows x 6 columns]

In [51]:
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [52]:
alt.Chart(df_200).mark_rect().encode(
    alt.X('hoursminutes(time):O', title='hour of day'),
    alt.Y('month(time):O', title='date'),
    alt.Color('wind_direction:Q', scale=alt.Scale(scheme='rainbow'))
)

/home/elilouis/mambaforge/envs/arm/lib/python3.11/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [53]:
alt.Chart(df_600).mark_rect().encode(
    alt.X('hoursminutes(time):O', title='hour of day'),
    alt.Y('month(time):O', title='date'),
    alt.Color('wind_direction:Q', scale=alt.Scale(scheme='rainbow'))
)

alt.Chart(...)

In [54]:
df_200['hour'] = df_200.time.dt.hour
df_200['doy'] = df_200.time.dt.day_of_year
df_200['weekofyear'] = df_200.time.apply(lambda dt: dt.isocalendar()[1])
df_200['start_doy'] = df_200['doy'] - 1

In [55]:
alt.Chart(df_200).mark_rect().encode(
    alt.X('hour:O', title='Hour of Day'),
    alt.Y("start_doy:Q", scale=alt.Scale(domain=[0,365], nice=False), title='Day of Year'),
    alt.Y2("doy:Q"),
    alt.Color('wind_direction:Q', scale=alt.Scale(scheme='rainbow'))
).properties(height=400)

/home/elilouis/mambaforge/envs/arm/lib/python3.11/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)

In [56]:
df_600['hour'] = df_600.time.dt.hour
df_600['doy'] = df_600.time.dt.day_of_year
df_600['weekofyear'] = df_600.time.apply(lambda dt: dt.isocalendar()[1])
df_600['start_doy'] = df_600['doy'] - 1

In [57]:
alt.Chart(df_600).mark_rect().encode(
    alt.X('hour:O', title='Hour of Day'),
    alt.Y("start_doy:Q", scale=alt.Scale(domain=[0,365], nice=False), title='Day of Year'),
    alt.Y2("doy:Q"),
    alt.Color('wind_direction:Q', scale=alt.Scale(scheme='rainbow'))
).properties(height=400)

/home/elilouis/mambaforge/envs/arm/lib/python3.11/site-packages/altair/utils/core.py:317: FutureWarning: iteritems is deprecated and will be removed in a future version. Use .items instead.
  for col_name, dtype in df.dtypes.iteritems():


alt.Chart(...)